In [351]:
from itertools import product

from sdanalysis.order import compute_neighbours, relative_orientations, relative_distances
from sdanalysis.figures import plot_frame, output_notebook, show
from sdanalysis import HoomdFrame
import gsd.hoomd

import numpy as np
from sklearn import cluster, decomposition, preprocessing

import warnings
warnings.filterwarnings('ignore')

import sys
sys.path.append('../src')
from trimer import plot_clustering

output_notebook()

ImportError: cannot import name 'output_notebook'

In [350]:
crystals = ["p2", "p2gg", "pg"]
# temps = ["0.30", "0.35", "0.40", "0.45"]
temps = ["0.40"]
snap = []
fname = "../data/simulation/trimer/dump-Trimer-P1.00-T{temp}-{crystal}.gsd"
for crystal, temp in product(crystals, temps):
    with gsd.hoomd.open(fname.format(temp=temp, crystal=crystal)) as trj:
        try:
            snap.append(HoomdFrame(trj[-1]))
        except IndexError:
            pass

## Simple Clustering

In [339]:
orient = [relative_orientations(s.box, s.position, s.orientation) for s in snap]
X = np.concatenate(orient, axis=0)

In [340]:
fig = plot_clustering(cluster.KMeans(n_clusters=3), X, snap)
show(fig)

In [341]:
fig = plot_clustering(cluster.DBSCAN(min_samples=8), X, snap)
show(fig)

In [342]:
fig = plot_clustering(cluster.MeanShift(cluster_all=False), X, snap)
show(fig)

In [343]:
fig = plot_clustering(cluster.AgglomerativeClustering(n_clusters=3, linkage='ward'), X, snap)
show(fig)

## Adding additional Dimensions


In [344]:
orient = [relative_orientations(s.box, s.position, s.orientation) for s in snap]
distance = [relative_distances(s.box, s.position) for s in snap]
for d in distance:
    d[np.isnan(d)] = 0
combined = [np.concatenate((o, d), axis=1) for o, d in zip(orient, distance)]
X_c = np.concatenate(combined, axis=0)

/home/malcolm/Projects/statdyn-analysis/src/sdanalysis/order.py:151: FreudDeprecationWarning: The getRsqList function is deprecated in favor of the r_sq_list class attribute and will be removed in a future version of freud.
  return np.sqrt(neighbours.getRsqList())
/home/malcolm/Projects/statdyn-analysis/src/sdanalysis/order.py:151: RuntimeWarning: invalid value encountered in sqrt
  return np.sqrt(neighbours.getRsqList())


In [345]:
fig = plot_clustering(cluster.KMeans(n_clusters=4), X, snap)
show(fig)

In [346]:
fig = plot_clustering(cluster.DBSCAN(), X_c, snap)
show(fig)

/home/malcolm/.miniconda/envs/MLCrystals/lib/python3.6/site-packages/bokeh/models/mappers.py:82: UserWarning: Palette length does not match number of factors. ['9'] will be assigned to `nan_color` gray
  warnings.warn("Palette length does not match number of factors. %s will be assigned to `nan_color` %s" % (extra_factors, self.nan_color))


## Clustering in Reduced Dimensionality

In [300]:
pca = decomposition.KernelPCA(kernel='rbf', n_components=6)
X_t = pca.fit_transform(X)

In [301]:
fig = plot_clustering(cluster.KMeans(n_clusters=3), X_t, snap)
show(fig)

In [302]:
fig = plot_clustering(cluster.KMeans(n_clusters=3), X, snap)
show(fig)

In [303]:
fig = plot_clustering(cluster.DBSCAN(), X_t, snap)
show(fig)

## Starting with more data

In [304]:
orient = [relative_orientations(s.box, s.position, s.orientation) for s in snap]
distance = [relative_distances(s.box, s.position) for s in snap]
for d in distance:
    d[np.isnan(d)] = 0
combined = [np.concatenate((o, d), axis=1) for o, d in zip(orient, distance)]
X_c = np.concatenate(combined, axis=0)

/home/malcolm/Projects/statdyn-analysis/src/sdanalysis/order.py:151: FreudDeprecationWarning: The getRsqList function is deprecated in favor of the r_sq_list class attribute and will be removed in a future version of freud.
  return np.sqrt(neighbours.getRsqList())
/home/malcolm/Projects/statdyn-analysis/src/sdanalysis/order.py:151: RuntimeWarning: invalid value encountered in sqrt
  return np.sqrt(neighbours.getRsqList())


In [320]:
X_cn = preprocessing.Normalizer().fit_transform(X_c)

In [324]:
pca = decomposition.KernelPCA(kernel='linear', n_components=8)
X_tc = pca.fit_transform(X_cn)

In [325]:
fig = plot_clustering(cluster.KMeans(n_clusters=4), X_tc, snap)
show(fig)

In [326]:
fig = plot_clustering(cluster.DBSCAN(), X_tc, snap)
show(fig)